# Creating a custom kernel
Vehicle model is not part of the standard dependencies part of jhub.
We need to create a custom kernel with all the dependencies we need.

Run the following 2 cells, and after it's done reload the page and select the kernels name `test`:

[Kernel] -> [Change kernel] -> "test"

See [Creating your own kernel](https://git.zooxlabs.com/zooxco/driving/tree/master/infra/jupyterhub#creating-your-own-kernel)

If you are running this notebook from the driving repo, you will need to run the setup script to update to the latest bazel version, or create_custom_kernel will error out.

In the jhub terminal run:

`./scripts/setup/setup.sh dev --tags bazel`

In [1]:
from infra.jupyterhub.user_utils.custom_kernel import create_custom_kernel

In [2]:
create_custom_kernel(
    kernel_name="test",
    dependencies=[
        "//sim/simple_sim/vehicle_sim:vehicle_model_py",
        "//data/tools:zed",
        "//data/tools/zplot2",
    ])

Building from local changes
Reload page to use kernel 'test'


# Using external dependencies

If you want to use any external dependencies that are not included in jhub by default (such as scipy), you will need to manually install the requirements. You will be then able to use them until you re-start the server. This will work if you are directly executing this from the jhub with the default repo, without updating it.

In [3]:
!pip3.6 install scipy

Traceback (most recent call last):
  File "/usr/local/bin/pip3.6", line 7, in <module>
    from pip import main
  File "/usr/local/lib/python3.6/dist-packages/pip/__init__.py", line 26, in <module>
    from pip.utils import get_installed_distributions, get_prog
  File "/usr/local/lib/python3.6/dist-packages/pip/utils/__init__.py", line 27, in <module>
    from pip._vendor import pkg_resources
  File "/usr/local/lib/python3.6/dist-packages/pip/_vendor/pkg_resources/__init__.py", line 3018, in <module>
    @_call_aside
  File "/usr/local/lib/python3.6/dist-packages/pip/_vendor/pkg_resources/__init__.py", line 3004, in _call_aside
    f(*args, **kwargs)
  File "/usr/local/lib/python3.6/dist-packages/pip/_vendor/pkg_resources/__init__.py", line 3046, in _initialize_master_working_set
    dist.activate(replace=False)
  File "/usr/local/lib/python3.6/dist-packages/pip/_vendor/pkg_resources/__init__.py", line 2578, in activate
    declare_namespace(pkg)
  File "/usr/local/lib/python3.6/dist-p

If you have pulled the repo, instead install it in your terminal:

`sudo pip3 install scipy`

Now we re-start the kernel:

- [Kernel] -> "Restart kernel)
- or the circulor arrow in the menu bar

And we can import scipy

In [1]:
import scipy

# Let's continue

In [3]:
from vehicle.common.proto.hero_state_pb2 import HeroState
from vehicle.common.proto.controller_pb2 import LowLevelControl
from vehicle.common.proto.drive_direction_enum_pb2 import DriveDirection
from vehicle.common.proto.drive_gear_enum_pb2 import DriveGear
from vehicle.common.entity.proto.vehicle_config_pb2 import VehicleParameters
from sim.simple_sim.vehicle_sim import vehicle_model_py
import copy
import numpy as np

Import a vehicle model from an existing run. In this example we use our recently simulated run.

In [4]:
uri = PASTE URI HERE
model = vehicle_model_py.create_from_uri(uri, vehicle_model="llc")

Set the state and controls

In [5]:
state = HeroState()
state.drive_direction = DriveDirection.kNorth
state.drive_gear = DriveGear.kForward
state.body_velocity.v_x = 10.0
state.pose_to_axle_dist = 0
state.steering_angle_north = 0.0
state.steering_angle_south = 0.0
state.body_acceleration.a_x = 0.0
state.local_utm_t_utm.SetInParent()
state.smooth_t_baselink.SetInParent()
state.pose.SetInParent()

In [6]:
control = LowLevelControl()
control.drive_direction = DriveDirection.kNorth
control.drive_gear = DriveGear.kForward

We will be breakin and steering 30 degrees

In [7]:
control.acceleration = -2.0
control.steering_angle_front = 2*np.pi/360*30

In [8]:
model.initialize(int(0), state)

In [9]:
states = [copy.deepcopy(state)]
for t in np.arange(0, 3e9, 5e6):
    state = model.step(int(t), control, state)
    state.time = t / 1e9
    states.append(copy.deepcopy(state))

In [10]:
from data.tools import zplot2 as zp
zp.set_output_format(zp.JupyterNotebook)

time = [e.time for e in states]
v_x = [e.body_velocity.v_x for e in states]
v_y = [e.body_velocity.v_y for e in states]
pose_x = [e.pose.x for e in states]
pose_y = [e.pose.y for e in states]

zp.figure(x_label="Time", y_label="Velocity", show_title=True, legend=True, grid=True)
zp.plot(x=time, y=v_x, name="Velocity X", linespec="b-")
zp.plot(x=time, y=v_y, name="Velocity Y", linespec="r-")
zp.figure(x_label="X", y_label="Y", name="Pose", show_title=True, legend=True, grid=True)
zp.plot(x=pose_x, y=pose_y, name="Hero Pose", linespec="b-")
zp.show()

Loading BokehJS ...